In [1]:
#Calling the necessary library
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
from art.attacks.evasion import ZooAttack
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error,r2_score
import platform
from sklearn.metrics import accuracy_score, recall_score, precision_score, f1_score
from art.estimators.classification import SklearnClassifier

/Applications/anaconda3/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/Applications/anaconda3/lib/python3.11/site-packages/art/estimators/certification/__init__.py:29: UserWarning: PyTorch not found. Not importing DeepZ or Interval Bound Propagation functionality
  warnings.warn("PyTorch not found. Not importing DeepZ or Interval Bound Propagation functionality")


In [2]:
cd "../"

/Users/jahidhasanpolash/Documents/Study/Summer2023/Covid_AI_Research_Lab/Machine_Learning


In [3]:
cd "../"

/Users/jahidhasanpolash/Documents/Study/Summer2023/Covid_AI_Research_Lab


In [4]:
#Reading the pre_processed data

os_type = platform.system()
if os_type.startswith("Darwin"): #for macOS
    data = pd.read_excel(r"dataset/processed_data/main/merged_scored_dataset1.xlsx")
else: 
    data = pd.read_excel(r"dataset\processed_data\main\merged_scored_dataset1.xlsx")
#Creating flag col depending on the quartile
data['flag'] = 1  # Initialize the 'flag' column with 3
data.loc[data['Laboratory confirmed, since the beginning of the pandemic Hospitalized'] <= 449, 'flag'] = 0
#data.loc[data['Laboratory confirmed, since the beginning of the pandemic Hospitalized'] <= 290, 'flag'] = 1
target_col = data["flag"]

In [5]:
data.head()

District  \
0      Ahrweiler   
1   Altenkirchen   
2    Alzey-Worms   
3   Bad Dürkheim   
4  Bad Kreuznach   

   Laboratory confirmed, since the beginning of the pandemic TOTAL  \
0                                               4577                 
1                                               4956                 
2                                               5130                 
3                                               4499                 
4                                               6121                 

   Laboratory confirmed, since the beginning of the pandemic Difference from  \
0                                                  4                           
1                                                  0                           
2                                                  1                           
3                                                  1                           
4                                                  0                           

   Laboratory confirmed, since the beginning of the pandemic Hospitalized  \
0                                                199                        
1                                                411                        
2                                                304                        
3                                                305                        
4                                                160                        

   Laboratory confirmed, since the beginning of the pandemic Deceased  \
0                                               52.0                    
1                                              101.0                    
2                                              123.0                    
3                                              150.0                    
4                                              142.0                    

   Laboratory confirmed, since the beginning of the pandemic RecoveredA  \
0                                               4423                      
1                                               4833                      
2                                               4970                      
3                                               4303                      
4                                               5923                      

   Laboratory confirmed, since the beginning of the pandemic Current CasesB  \
0                                                102                          
1                                                 22                          
2                                                 37                          
3                                                 46                          
4                                                 56                          

   Reported, the last 7 days,Incidence per 100, Incidence per 100 ,+USAFD  \
0                                               50.0                        
1                                                8.5                        
2                                                9.3                        
3                                               14.3                        
4                                               18.3                        

   Reported, the last 7 days,Incidence per 100, Incidence per 100 ,<20 Jahre  \
0                                              132.2                           
1                                                8.4                           
2                                               24.0                           
3                                               21.6                           
4                                               41.4                           

   Reported, the last 7 days,Incidence per 100, Incidence per 100 ,20-59 JahreE  \
0                                               49.0                              
1                                              

In [ ]:
# Finding highly correlated features
import seaborn as sns
import matplotlib.pyplot as plt

# Assuming 'data' is your DataFrame
correlation_matrix = data.corr()

# Create a heatmap
plt.figure(figsize=(10, 8))
sns.heatmap(correlation_matrix, annot=True, cmap='coolwarm', fmt=".2f", linewidths=0.5)
plt.title("Correlation Heatmap")
plt.show()

In [6]:
#data.head()
#Droping the highly correlated features
features = data.drop("Laboratory confirmed, since the beginning of the pandemic Hospitalized", axis=1)
#Droping district as it is now represented as cluster
features = features.drop("District",axis=1)
features = features.drop("Laboratory confirmed, since the beginning of the pandemic TOTAL",axis=1)
features = features.drop("Laboratory confirmed, since the beginning of the pandemic RecoveredA",axis=1)
features = features.drop("Laboratory confirmed, since the beginning of the pandemic Deceased",axis=1)
#droping the terget col
features = features.drop("flag",axis = 1)
features.head()

Laboratory confirmed, since the beginning of the pandemic Difference from  \
0                                                  4                           
1                                                  0                           
2                                                  1                           
3                                                  1                           
4                                                  0                           

   Laboratory confirmed, since the beginning of the pandemic Current CasesB  \
0                                                102                          
1                                                 22                          
2                                                 37                          
3                                                 46                          
4                                                 56                          

   Reported, the last 7 days,Incidence per 100, Incidence per 100 ,+USAFD  \
0                                               50.0                        
1                                                8.5                        
2                                                9.3                        
3                                               14.3                        
4                                               18.3                        

   Reported, the last 7 days,Incidence per 100, Incidence per 100 ,<20 Jahre  \
0                                              132.2                           
1                                                8.4                           
2                                               24.0                           
3                                               21.6                           
4                                               41.4                           

   Reported, the last 7 days,Incidence per 100, Incidence per 100 ,20-59 JahreE  \
0                                               49.0                              
1                                               12.1                              
2                                                4.4                              
3                                               19.5                              
4                                               20.0                              

   Reported, the last 7 days,Incidence per 100, Incidence per 100 ,>=60 Jahre  \
0                                                7.1                            
1                                                2.6                            
2                                                8.2                            
3                                                2.3                            
4                                                2.0                            

   Recovery Rate  Hospitalization Rate     Score  Cluster  
0       0.775972              0.176385  0.299794        1  
1       0.785770              0.348355  0.218708        5  
2       0.769890              0.269208  0.250341        4  
3       0.773656              0.284613  0.244521        4  
4       0.769510              0.080549  0.344480        2

In [7]:
X_train, X_test, y_train, y_test = train_test_split(features, target_col, test_size=0.3, random_state=29)

In [ ]:
mse_value = []
estimators_ = []
for estimator in range(30,170):
    RF_model = RandomForestRegressor(n_estimators = estimator ,random_state= 22)
    RF_model.fit(X_train,y_train)
    y_pred = RF_model.predict(X_test)
    estimators_.append(estimator)
    mse_value.append(mean_squared_error(y_test, y_pred))
     

In [ ]:
import matplotlib.pyplot as plt
plt.plot(estimators_, mse_value)
plt.title('mse')
plt.xlabel('estimator')
plt.ylabel('mse')
plt.show()

In [ ]:
plt.plot(estimators_[20:30], mse_value[20:30])
plt.title('mse')
plt.xlabel('estimator')
plt.ylabel('mse')
plt.show()

In [8]:
#Selecting 58 as estimator as it was the lowest mse
Random_forest_model_for_COVID = RandomForestClassifier(n_estimators=58, random_state= 22)
Random_forest_model_for_COVID.fit(X=X_train, y=y_train)
y_pred = Random_forest_model_for_COVID.predict(X_test)

In [9]:
#Evaluating the ML model before attack
accuracy = accuracy_score(y_test, y_pred)
recall = recall_score(y_test, y_pred,average='weighted')
precision = precision_score(y_test, y_pred,average='weighted')
f1 = f1_score(y_test, y_pred,average='weighted')

print(f"Accuracy: {accuracy:.2f}")
print(f"Recall: {recall:.2f}")
print(f"Precision: {precision:.2f}")
print(f"F1 Score: {f1:.2f}")

Accuracy: 0.98
Recall: 0.98
Precision: 0.98
F1 Score: 0.98


# Starting the Zoo Attack #

In [10]:
# Create ART classifier for scikit-learn RandomForestClassifier
art_classifier = SklearnClassifier(model=Random_forest_model_for_COVID)

# Create ART Zeroth Order Optimization attack
zoo = ZooAttack(classifier=art_classifier, confidence=0.0, targeted=False, learning_rate=1e-1, max_iter=20,
                binary_search_steps=10, initial_const=1e-3, abort_early=True, use_resize=False, 
                use_importance=False, nb_parallel=1, batch_size=1, variable_h=0.2)

 # Generate adversarial samples with ART Zeroth Order Optimization attack
Zoo_x_train_adv = zoo.generate(X_train.values)

/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
ZOO:   0%|                                            | 0/11690 [00:00<?, ?it/s]/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but 

ZOO:   0%|                                    | 1/11690 [00:00<19:43,  9.88it/s]/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but 

/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applicati

ZOO:   0%|                                    | 3/11690 [00:00<17:20, 11.24it/s]/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but 

/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applicati

...

/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applicati

/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applicati

/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applicati

/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/Applicati

KeyboardInterrupt: 

In [ ]:
np.save("Zoo_X_train.npy",Zoo_x_train_adv)

In [11]:
x_train_adv = np.load("Zoo_X_train.npy")

In [ ]:
x_test_adv = zoo.generate(X_test.values)

In [ ]:
np.save("Zoo_X_test.npy",x_test_adv)

In [12]:
x_test_adv = np.load("Zoo_X_test.npy")

In [13]:
import json

def print_average_perturbations(adv_data, original_data):
    # Compute the difference between the original and adversarial samples
    perturbations = adv_data - original_data
    # Calculate the average perturbation for each feature
    average_perturbations = np.mean(np.abs(perturbations), axis=0)

    result_dict = dict(zip(original_data.columns, average_perturbations))

    print(json.dumps(result_dict, indent=2))

In [15]:
print_average_perturbations(x_test_adv, X_test)
print_average_perturbations(x_train_adv, X_train)

{
  "Laboratory confirmed, since the beginning of the pandemic Difference from": 0.00011976005550392136,
  "Laboratory confirmed, since the beginning of the pandemic Current CasesB": 5.988024041324318e-05,
  "Reported, the last 7 days,Incidence per 100, Incidence per 100 ,+USAFD": 0.000618762036640487,
  "Reported, the last 7 days,Incidence per 100, Incidence per 100 ,<20 Jahre": 0.0004655145430758952,
  "Reported, the last 7 days,Incidence per 100, Incidence per 100 ,20-59 JahreE": 0.0015964702426078553,
  "Reported, the last 7 days,Incidence per 100, Incidence per 100 ,>=60 Jahre": 0.0005050939505923532,
  "Recovery Rate": 0.04465094398640999,
  "Hospitalization Rate": 0.0597182603183056,
  "Score": 0.0505455201959222,
  "Cluster": 0.0005301920061339875
}
{
  "Laboratory confirmed, since the beginning of the pandemic Difference from": 0.0002565672603603915,
  "Laboratory confirmed, since the beginning of the pandemic Current CasesB": 0.00010239032787885086,
  "Reported, the last 7 da

In [16]:
#Evaluating the ML model after attack
y_pred_adv = Random_forest_model_for_COVID.predict(x_test_adv)
accuracy = accuracy_score(y_test, y_pred_adv)
recall = recall_score(y_test, y_pred_adv,average='weighted')
precision = precision_score(y_test, y_pred_adv,average='weighted')
f1 = f1_score(y_test, y_pred_adv,average='weighted')

print(f"Accuracy: {accuracy:.2f}")
print(f"Recall: {recall:.2f}")
print(f"Precision: {precision:.2f}")
print(f"F1 Score: {f1:.2f}")

Accuracy: 0.45
Recall: 0.45
Precision: 0.44
F1 Score: 0.43


/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


# Retaining with Adverserial data #

In [17]:
#Selecting 58 as estimator as it was the lowest mse
random_forest_model_with_adv_data = Random_forest_model_for_COVID.fit(X=x_train_adv, y=y_train)
y_pred_with_retain_adv_data = random_forest_model_with_adv_data.predict(X_test)

/Applications/anaconda3/lib/python3.11/site-packages/sklearn/base.py:458: UserWarning: X has feature names, but RandomForestClassifier was fitted without feature names
  warnings.warn(


In [18]:
#Evaluating the ML model before attack
accuracy = accuracy_score(y_test, y_pred_with_retain_adv_data)
recall = recall_score(y_test, y_pred_with_retain_adv_data,average='weighted')
precision = precision_score(y_test, y_pred_with_retain_adv_data,average='weighted')
f1 = f1_score(y_test, y_pred_with_retain_adv_data,average='weighted')

print(f"Accuracy: {accuracy:.2f}")
print(f"Recall: {recall:.2f}")
print(f"Precision: {precision:.2f}")
print(f"F1 Score: {f1:.2f}")

Accuracy: 0.89
Recall: 0.89
Precision: 0.90
F1 Score: 0.89


In [19]:
#Selecting 58 as estimator as it was the lowest mse
y_pred_with_retain_adv_data_x_test_adv = random_forest_model_with_adv_data.predict(x_test_adv)

In [20]:
#Evaluating the ML model before attack
accuracy = accuracy_score(y_test, y_pred_with_retain_adv_data_x_test_adv)
recall = recall_score(y_test, y_pred_with_retain_adv_data_x_test_adv,average='weighted')
precision = precision_score(y_test, y_pred_with_retain_adv_data_x_test_adv,average='weighted')
f1 = f1_score(y_test, y_pred_with_retain_adv_data_x_test_adv,average='weighted')

print(f"Accuracy: {accuracy:.2f}")
print(f"Recall: {recall:.2f}")
print(f"Precision: {precision:.2f}")
print(f"F1 Score: {f1:.2f}")

Accuracy: 0.96
Recall: 0.96
Precision: 0.96
F1 Score: 0.96
